In [1]:
# n number of subsequences of a patient's notes
# c is scaling factor and controls influence of number of subsequences 
# use c= 2
# pmax is max probability of readmission
# pmean is mean probability of readmission
from datasets import load_dataset
import os
import numpy as np
import torch
from scipy.special import softmax

In [2]:
from transformers import DistilBertTokenizerFast
#tokenizer = DistilBertTokenizerFast.from_pretrained('emilyalsentzer/Bio_ClinicalBERT')
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')

/home/ubuntu/.local/lib/python3.8/site-packages/torch/cuda/__init__.py:52: UserWarning: CUDA initialization: Found no NVIDIA driver on your system. Please check that you have an NVIDIA GPU and installed a driver from http://www.nvidia.com/Download/index.aspx (Triggered internally at  /pytorch/c10/cuda/CUDAFunctions.cpp:100.)
  return torch._C._cuda_getDeviceCount() > 0


In [21]:
def encode(examples):
     return tokenizer(examples['text'], truncation=True, padding='max_length', max_length=512)

Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-911751613882cd5b/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab/cache-08cd88405307efd2.arrow


In [22]:
# training model on tokenized and split data
class Dataset(torch.utils.data.Dataset):
    def __init__(self, inputs, labels):
        self.inputs = inputs
        self.labels = labels

    def __getitem__(self, idx):
        item = {key: torch.tensor(val) for key, val in self.inputs[idx].items() if key != 'text'}
        item['labels'] = torch.tensor(int(self.labels[idx]['text']))
        return item

    def __len__(self):
        return len(self.labels)

In [26]:
def probability(test_dataset):
    # generates prediction from model
    pred = trainer.predict(test_dataset).predictions
    # softmax each row so each row sums to 1
    prob = softmax(pred, axis = 1)
    # find the mean probability of readmission
    meanprob = np.mean(prob,axis=0)[1]
    # find the max probability of readmission
    maxprob = np.amax(prob,axis=0)[1]
    
    n = pred.shape[0]
    
    return meanprob, maxprob, n

In [28]:
def prepare_data(patientID):
    # loading features and labels per patient
    input_dataset = load_dataset('text', data_files={'test': '../data/processPatient/'+patientID})
    label_dataset = load_dataset('text', data_files={'test': '../data/labels/'+patientID})
    
    # applying encoding function to dataset
    input_dataset = input_dataset.map(encode, batched=True)
    
    # setting dataset to testing dataset
    test_dataset = Dataset(input_dataset['test'], label_dataset['test'])
    
    return test_dataset

In [31]:
def readmit_probability(maxprob,meanprob,n):
    # c accounts for patients with many notes
    c=2
    # weight as n/c
    scaling = n/c
    denominator = 1+scaling
    numerator = maxprob + (meanprob * scaling)
    
    probability = numerator/denominator
    return probability

In [7]:
from transformers import DistilBertForSequenceClassification, Trainer, TrainingArguments
model = DistilBertForSequenceClassification.from_pretrained("distilbert-base-uncased")

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_transform.bias', 'vocab_layer_norm.weight', 'vocab_layer_norm.bias', 'vocab_projector.weight', 'vocab_projector.bias']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'pre_classifier.bias', 'classi

In [32]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, roc_auc_score

trainer = Trainer(
    model=model                        # the instantiated 🤗 Transformers model to be trained
)

Using custom data configuration default
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-c351ed3ddfb4579f/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab)
Using custom data configuration default
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-2235f4a50ed1aa95/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab)
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-c351ed3ddfb4579f/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab/cache-50af1ab6a39d0389.arrow


In [ ]:
# empty list of scalable readmission prediction probabilities
patient_prob = []

# generate list of all patients
patients = os.listdir('../data/processPatient/')

for i in range(len(patients)):
    # load the patient datset
    test_dataset = prepare_data(patients[i])
    # find the max and mean probability of readmission
    mean, maximum, n = probability(test_dataset)
    readmit = readmit = readmit_probability(mean,maximum,n)
    patient_prob.append(readmit)

Using custom data configuration default
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-0ccdf49cc30b8d90/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab)
Using custom data configuration default
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-296cbf505275ecc4/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab)
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-0ccdf49cc30b8d90/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab/cache-efa1a46174fd5182.arrow
Using custom data configuration default
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-7bd1780792922f30/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab)
Using custom data configuration default
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-d02dd922e6a04b82/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca

Using custom data configuration default


Dataset text downloaded and prepared to /home/ubuntu/.cache/huggingface/datasets/text/default-a168161829e2d513/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab. Subsequent calls will reuse this data.


Dataset text downloaded and prepared to /home/ubuntu/.cache/huggingface/datasets/text/default-3d5f9b8aa6fc68fb/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab. Subsequent calls will reuse this data.


Using custom data configuration default


...

Dataset text downloaded and prepared to /home/ubuntu/.cache/huggingface/datasets/text/default-254141249beedc1c/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab. Subsequent calls will reuse this data.


Using custom data configuration default


Using custom data configuration default


Dataset text downloaded and prepared to /home/ubuntu/.cache/huggingface/datasets/text/default-347057c639c5daa7/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab. Subsequent calls will reuse this data.


Dataset text downloaded and prepared to /home/ubuntu/.cache/huggingface/datasets/text/default-a9e15af415774ce0/0.0.0/daf90a707a433ac193b369c8cc1772139bb6cca21a9c7fe83bdd16aad9b9b6ab. Subsequent calls will reuse this data.


In [33]:
print(mean)
print(maximum)
print(n)
print(readmit)

0.51406866
0.53015363
29
0.5291158922256962


In [38]:
print(len(patient_prob))

2141


In [36]:
print(patients)

['24394', '10198', '13572', '14119', '9758', '8587', '3323', '22563', '18650', '48601', '66214', '2259', '2374', '50893', '15474', '58071', '51712', '30461', '24797', '3342', '40440', '43615', '41163', '27068', '15144', '30266', '23281', '91905', '19424', '11762', '29965', '97768', '19301', '83496', '91158', '5950', '25227', '5002', '16252', '31221', '15090', '27372', '52183', '60805', '27267', '82178', '52389', '10049', '85019', '27260', '57138', '88638', '42968', '7008', '31707', '75054', '59299', '43926', '15181', '62829', '49015', '22527', '99165', '25378', '60545', '12689', '16911', '5830', '80053', '2341', '32138', '83441', '47747', '97728', '18348', '17151', '7216', '8581', '76580', '52592', '59674', '53290', '45619', '50828', '29524', '30287', '24476', '680', '6695', '44920', '32673', '47091', '14741', '99441', '7296', '68673', '90171', '23895', '746', '89347', '16932', '70886', '20321', '14495', '70441', '25', '368', '22700', '96913', '85095', '30848', '3571', '25686', '14642'